### Create target 

We want to predict a spending of active customers in next 2 weeks. 

Let's create at target that measures sum of invoice Amount for the customer over the next 14d period.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

21:58:14 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


21:58:14 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:58:15 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:58:15 | INFO     | No catalog activated.


21:58:15 | INFO     | 6 feature lists, 31 features deployed


...

21:58:15 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:58:16 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:58:16 | INFO     | No catalog activated.


21:58:16 | INFO     | 6 feature lists, 31 features deployed


21:58:17 | INFO     | Catalog activated: Grocery Dataset Tutorial


As we already know, Amount column is from GROCERYINVOICE table, that's why we need to create a view from it:

In [2]:
groceryinvoice_view = catalog.get_view("GROCERYINVOICE")

The target is a sum of the Amount column in next 14d:

In [3]:
target = groceryinvoice_view\
    .groupby(['GroceryCustomerGuid'])\
    .forward_aggregate(
        "Amount", method="sum",
        target_name="CUSTOMER_Sum_of_invoice_Amount_next_14d",
        window='14d',
        fill_value=0
    )

In order for a target (or a feature) to be recorded in catalog, we need to save it:

In [4]:
target.save()

Also we will update description of the target

In [5]:
target.update_description(
	"Sum of invoice Amount for the customer over the next 14d period."
)


Target is created. We can check target's definition file, which provides explicit outline of all operations for declaration of the target.
For example this definition includes implicit operations like all cleaning operations inherited from the table. 

In [6]:
target.definition

'# Generated by SDK version: 0.5.0.dev6\nfrom bson import ObjectId\nfrom featurebyte import ColumnCleaningOperation\nfrom featurebyte import DisguisedValueImputation\nfrom featurebyte import EventTable\nfrom featurebyte import ValueBeyondEndpointImputation\n\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("64ff1c910d5bfbfb21bce78a"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[\n        ColumnCleaningOperation(\n            column_name="Amount",\n            cleaning_operations=[\n                DisguisedValueImputation(\n                    imputed_value=None, disguised_values=[-99, -98]\n                ),\n                ValueBeyondEndpointImputation(\n                    type="less_than", end_point=0, imputed_value=0\n                ),\n                ValueBeyondEndpointImputation(\n                    type="greater_than", end_point=2000, imputed_value=2000\n                ),\n            ],\n        )\n    ],\n)\ntarget = event_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).forward_aggregate(\n    value_column="Amount",\n    method="sum",\n    window="14d",\n    target_name="CUSTOMER_Sum_of_invoice_Amount_next_14d",\n    skip_fill_na=True,\n)\nfeat = target["CUSTOMER_Sum_of_invoice_Amount_next_14d"]\nfeat_1 = feat.copy()\nfeat_1[feat.isnull()] = 0\nfeat_1.name = "CUSTOMER_Sum_of_invoice_Amount_next_14d"\noutput = feat_1\noutput.save(_id=ObjectId("64ff1cfb385e2ada5de0a15a"))\n'

### Concepts discussed in this tutorial 
- [More about feature definition file](https://docs.featurebyte.com/latest/about/glossary/#feature-definition-file)

#### SDK reference for
- [Target](https://docs.featurebyte.com/latest/reference/core/target/)
- [View.groupby()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)
- [GroupBy.forward_aggregate()](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.forward_aggregate/)
- [Aggregation functions](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)
- [Feature.definition](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)
